In [1]:
from database.strategy import Strategy
from database.sec import SEC
from database.market import Market
from transformer.date_transformer import DateTransformer
from transformer.model_transformer import ModelTransformer
from transformer.product_transformer import ProductTransformer
from transformer.predictor_transformer import PredictorTransformer
from preprocessor.model_preprocessor import ModelPreprocessor
from preprocessor.predictor_preprocessor import PredictorPreprocessor
from modeler.modeler import Modeler as sp
from utils.date_utils import DateUtils
import pandas as pd
import matplotlib.pyplot as plt
from datetime import datetime, timedelta, timezone
from tqdm import tqdm
import math

In [11]:
## Loading Constants
start = "2008-01-01"
end = datetime(2021,12,31).strftime("%Y-%m-%d")
# Loading Databases
strat_db = Strategy("unity")
market = Market()
sec = SEC("sec")
market.connect()
tickers = market.retrieve_data("sp500").sort_values("Symbol")
market.close()
quarterly_range = range(1,5)
yearly_range = range(2018,2021)
model_range = range(len(tickers["Symbol"]))

In [3]:
strat_db.connect()
bond_sim = strat_db.retrieve_data("bond_quarterly_sim")
fund_sim = strat_db.retrieve_data("fundamental_quarterly_sim")
strat_db.close()

In [4]:
fund_sim.columns

Index(['_id', 'year', 'quarter',
       'quarterly_fundamental_classification_prediction',
       'quarterly_fundamental_classification_score',
       'quarterly_fundamental_regression_prediction',
       'quarterly_fundamental_regression_score', 'ticker'],
      dtype='object')

In [5]:
final = fund_sim.drop("_id",axis=1).merge(bond_sim.drop("_id",axis=1),on=["year","quarter","ticker"],how="left")

In [6]:
final

year  quarter  quarterly_fundamental_classification_prediction  \
0      2015        1                                                1   
1      2015        1                                                1   
2      2015        1                                                1   
3      2015        1                                                1   
4      2015        1                                                1   
...     ...      ...                                              ...   
12295  2021        4                                                1   
12296  2021        4                                                0   
12297  2021        4                                                1   
12298  2021        4                                                0   
12299  2021        4                                                0   

       quarterly_fundamental_classification_score  \
0                                            0.75   
1                                            0.75   
2                                            0.50   
3                                            0.50   
4                                            0.75   
...                                           ...   
12295                                        0.60   
12296                                        0.60   
12297                                        0.80   
12298                                        0.80   
12299                                        0.80   

       quarterly_fundamental_regression_prediction  \
0                                        29.764845   
1                                        15.484882   
2                                        83.229851   
3                                        14.201034   
4                                        59.305409   
...                                            ...   
12295                                    18.565178   
12296                                    90.891281   
12297                                   135.920731   
12298                                   252.458801   
12299                                    28.970032   

       quarterly_fundamental_regression_score ticker  \
0                                    0.127575      A   
1                                    0.174229    AAL   
2                                    0.156128    AAP   
3                                    0.256157   AAPL   
4                                    0.192384    ABC   
...                                       ...    ...   
12295                                0.150889    XRX   
12296                                0.107342    YUM   
12297                                0.043811    ZBH   
12298                                0.178247   ZBRA   
12299                                0.108821   ZION   

       quarterly_bond_classification_prediction  \
0                                           1.0   
1                                           1.0   
2                                           1.0   
3                                           1.0   
4                                           1.0   
...                                         ...   
12295                                       0.0   
12296                                       1.0   
12297                                       1.0   
12298                                       1.0   
12299                                       0.0   

       quarterly_bond_classification_score  \
0                                     0.75   
1                                     0.75   
2                                     0.50   
3                                     0.50   
4                                     0.75   
...                                    ...   
12295                                 0.40   
12296                                 0.80   
12297                                 1.00   
12298                                 0.80   
12299                                 0.60   

     

In [7]:
market.connect()
ranks = market.retrieve_data("quarter_ranked")
market.close()

In [8]:
ranks

_id  year  quarter ticker        high         low  \
0      5ff07ceaff844f4439f37aa6  2008        1    UAL   32.535082   30.182787   
1      5ff07ceaff844f4439f37aa7  2008        1    DAL   14.832787   13.669016   
2      5ff07ceaff844f4439f37aa8  2008        1    AAL   12.655082   11.666229   
3      5ff07ceaff844f4439f37aa9  2008        1    HUM   69.960984   67.263934   
4      5ff07ceaff844f4439f37aaa  2008        1    UNH   47.795574   46.392459   
...                         ...   ...      ...    ...         ...         ...   
24300  5ff07cebff844f4439f3d992  2020        3   TSLA  365.226125  340.174626   
24301  5ff07cebff844f4439f3d993  2020        3    UAA   10.779375   10.291562   
24302  5ff07cebff844f4439f3d994  2020        3    IVZ   10.802500   10.386094   
24303  5ff07cebff844f4439f3d995  2020        3   ALGN  310.479687  299.284062   
24304  5ff07cebff844f4439f3d996  2020        3    TPR   15.085312   14.409687   

             open       close        volume    adjclose       week     delta  \
0       31.552787   31.472459  4.421859e+06   31.369443   7.262295 -0.580469   
1       14.311311   14.223770  5.833372e+06   12.634218   7.262295 -0.497441   
2       12.207705   12.149672  3.692672e+06   11.454000   7.262295 -0.495601   
3       68.732295   68.656229  4.428454e+06   63.071959   7.262295 -0.337649   
4       47.196721   47.059344  1.052349e+07   39.565312   7.262295 -0.295601   
...           ...         ...           ...         ...        ...       ...   
24300  352.975532  354.207405  8.106330e+07  354.207405  33.546875  0.435628   
24301   10.512812   10.527656  7.500042e+06   10.527656  33.546875  0.448219   
24302   10.592969   10.595781  6.231827e+06   10.418810  33.546875  0.467254   
24303  304.408125  305.265154  7.195062e+05  305.265154  33.546875  0.468585   
24304   14.754375   14.722969  5.948903e+06   14.722969  33.546875  0.713164   

        rank  
0        0.0  
1        1.0  
2        2.0  
3        3.0  
4        4.0  
...      ...  
24300  499.0  
24301  500.0  
24302  501.0  
24303  502.0  
24304  503.0  

[24305 rows x 13 columns]

In [12]:
sims = []
gap = 90
quarter_gap = int(gap/90)
training_years = 3
sims = []
sec.connect()
strat_db.connect()
market.connect()
strat_db.drop_table("ranked_quarterly_sim")
strat_db.drop_table("ranked_quarterly_sim_errors")
for year in tqdm(yearly_range):
    for quarter in tqdm(quarterly_range):
        try:
            ## Setting Up
            print(year,quarter)
            date_ranges = DateUtils.create_quarterly_training_range_rec(year,quarter,training_years,gap)
            training_start,training_end,prediction_start,prediction_end = date_ranges
            dates = pd.to_datetime(date_ranges)
            quarters = [x.quarter for x in dates]
            years = [x.year for x in dates]
            print(date_ranges)
            ### switch to all tickers
            for i in model_range:
                try:
                    ticker = tickers.iloc[i]["Symbol"].replace(".","-")
                    price = market.retrieve_price_data("prices",ticker)
                    rank = ranks[ranks["ticker"] == ticker]
                    fqd = final[final["ticker"]==ticker]
                    mt = ModelTransformer(ticker,training_start,training_end,gap)
                    mr = ModelPreprocessor(ticker)
                    prot = ProductTransformer(ticker,prediction_start,prediction_end)
                    ## ranking_model
                    rank_data = rank.drop(["_id","week","ticker","adjclose"],axis=1).merge(fqd.drop("ticker",axis=1),on=["year","quarter"],how="left")
                    rkpd = mt.quarterly_rank_transform(rank_data,ticker,years[0],quarters[0]
                                                       ,years[1],quarters[1],quarter_gap)
                    kpd = mr.rank_preprocess(rkpd.copy(),ticker)
                    rkfr = sp.regression(kpd,ranked=True,tf=True)
                    fundamental_results = pd.DataFrame([rkfr])
                    product_refineds = []
                    product_qpds = []
                    for i in range(len(fundamental_results)):
                        fundamental_result = fundamental_results.iloc[i]
                        if fundamental_result["model_type"] == "ranked":
                            product_refined = kpd
                        elif fundamental_result["model_type"] == "regression":
                            product_refined = rpd
                        else:
                            product_refined = cpd
                        product_refineds.append(product_refined)
                    sim = prot.merge_quarterlies_rank(product_refineds,fundamental_results,"ranked")
                    strat_db.store_data("ranked_quarterly_sim",pd.DataFrame([sim]))
                except Exception as e:
                    message = {"status":"quarterly modeling","ticker":ticker,"year":str(year),"quarter":str(quarter),"message":str(e)}
                    print(message)
                    strat_db.store_data("ranked_quarterly_sim_errors",pd.DataFrame([message]))
        except Exception as e:
            print(year,quarter,str(e))
sec.close()
market.close()
strat_db.close()

  0%|                                                                                                                                                                                                     | 0/4 [00:00<?, ?it/s]

2018 1
['2015-01-01', '2018-01-01', '2018-01-01', '2018-04-02']

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

1/1 [==============================] - 0s 2ms/step - loss: 59.1668 - mean_absolute_percentage_error: 59.1668

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='f

1/1 [==============================] - 0s 2ms/step - loss: 335.7314 - mean_absolute_percentage_error: 335.7314

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

1/1 [==============================] - 0s 1ms/step - loss: 87.8020 - mean_absolute_percentage_error: 87.8020

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float

1/1 [==============================] - 0s 3ms/step - loss: 39.8717 - mean_absolute_percentage_error: 39.8717

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

1/1 [==============================] - 0s 2ms/step - loss: 67.3937 - mean_absolute_percentage_error: 67.3937

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32

1/1 [==============================] - 0s 2ms/step - loss: 46.7069 - mean_absolute_percentage_error: 46.7069

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

1/1 [==============================] - 0s 2ms/step - loss: 83.7232 - mean_absolute_percentage_error: 83.7232

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32

...


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

1/1 [==============================] - 0s 2ms/step - loss: 64.3416 - mean_absolute_percentage_error: 64.3416

If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this 


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float64, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float32 by default, call `tf.keras.backend.set_floatx('float32')`. To change just this layer, pass dtype='float32' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [5:24:15<00:00, 6485.02s/it]
